In [1]:
# Range dependent Hamiltonian Algorithm for numerical QUBO formulation

# This code only use one subdomain because of time limit of D-Wave account
# For a genearal code, please use additional "for" loop in "cef2"

# 32 by 32 matrix A
# Range of x_i = (-128, 127)
# Subrange of x_i = (0, 3) = q_(i,1) + 2q(i,2)

import numpy as np
import random, math
import copy
import sys
import math

Dimension = 32
A = np.random.randint(-10, 10, size=(Dimension,Dimension))
np.set_printoptions(threshold=sys.maxsize)
print("Matrix A:")
print(A)

x_fin = np.random.randint(-128, 127, size=Dimension)
print("\nSolution vector x:")
print(x_fin)

b = np.dot(A, x_fin)
print("\nVector b:")
print(b)

Matrix A:
[[ -5  -6  -9   2   9   2  -8  -1   6  -6  -2  -8   6   2  -5  -7  -1   0
   -1  -8   9  -2   5  -8   6   2  -7   4   4  -6   5  -1]
 [ -3  -2  -2   7  -6   2  -7 -10  -4 -10  -2  -2   2  -9   9  -4   2  -2
    1 -10  -5  -5   7   0  -3  -2   7  -1   6  -8  -2   7]
 [  0  -6  -3  -4   9  -9   4  -4  -9   6   8  -2  -8   6   4  -7   9  -5
   -7   5  -8  -6   3   6   6  -8   4   1   4  -3   1 -10]
 [ -3  -8   7  -9  -9  -1  -8  -2   7  -6  -1  -9   2   4  -1  -9 -10  -1
   -2  -8   8   2  -2  -5  -9   5   0  -2   5   5  -5 -10]
 [  2   1   1  -6   5  -5  -3  -9   2   0  -5   4   3   1  -3   2   6  -4
   -6  -6   8   3  -3  -4  -1  -4   8  -2  -1   2  -8   9]
 [ -6   1   1   9 -10   8  -8  -5  -1  -8  -7   3   3   3  -9  -3   8   8
    6  -1   3   2  -4  -6  -7   4   7  -9  -7 -10  -3  -8]
 [  2   5   0  -6   8   4  -7  -9   8   4   5   3   4   8   5   2   1   8
   -8   9   9   4  -6   4  -9  -8  -2   5   3  -3   1 -10]
 [ -1  -7  -5   2  -1  -2 -10  -3   1   6  -8  -1   1   0  

In [2]:
qubits = 2
# Calculate translation number including solution vector x
Trs = np.zeros(Dimension)
x_qubit = np.zeros(Dimension)
sub_size = pow(2,qubits)
for k in range(Dimension):
    Val = divmod(x_fin[k], sub_size)
    Trs[k] = sub_size*Val[0]
    x_qubit[k] = Val[1]
print("Translation vector T:")
print(Trs)
print("\nQubit notation:")
print(x_qubit)
c = b - np.dot(A, Trs)
print("\nUpdated vector c:")
print(c)

Translation vector T:
[-128.   16.  -96.   12.    8.  -60.   76.  -20.  -24. -104. -116.  116.
   36.  -80.   16.   68.   24.    4.  -80. -124.   20.  -88. -120.   44.
    4. -108.   44.   56.    0. -108.    8.  108.]

Qubit notation:
[2. 2. 3. 3. 0. 1. 2. 0. 0. 3. 3. 3. 2. 3. 1. 2. 1. 0. 2. 0. 2. 1. 1. 0.
 3. 2. 3. 0. 2. 0. 1. 1.]

Updated vector c:
[ -75.  -50.  -17. -116.    9.  -17.   12. -110. -107.   16.  -25.  -11.
 -146. -100.  -73.   63.  -51.   44.  124. -147. -101.  -48.  101.  -34.
  -36.  -31.  -16.  -37.  -12.    9.   47.  -54.]


In [3]:
QM = np.zeros((qubits*Dimension, qubits*Dimension))
### Linear terms ###
for k in range(Dimension):
    for i in range(Dimension):
        for l in range(qubits):
            cef1 = pow(2,2*l)*pow(A[k][i],2)
            cef2 = pow(2,l+1)*A[k][i]*c[k]
            po = qubits*i + l
            QM[po][po] = QM[po][po] + cef1 - cef2
 
### First quadratic term ### 
for k in range(Dimension):
    for i in range(Dimension):
        for l1 in range(qubits-1):
            for l2 in range(l1+1,qubits):
                qcef = pow(2, l1+l2+1)*pow(A[k][i],2)
                po1 = qubits*i + l1
                po2 = qubits*i + l2
                QM[po1][po2] = QM[po1][po2] + qcef
 
### Second quadratic term ### 
for k in range(Dimension):
    for i in range(Dimension-1):
        for j in range(i+1,Dimension):
            for l1 in range(qubits):
                for l2 in range(qubits):  
                    qcef = pow(2, l1+l2+1)*A[k][i]*A[k][j] 
                    po1 = qubits*i + l1
                    po2 = qubits*j + l2
                    QM[po1][po2] = QM[po1][po2] + qcef

# Print Matrix Q
print("# Matrix Q is")
print(QM)
print("\nMinimum energy is ",-np.dot(c,c))
print("\n")

# Print Python code for the run in D-Wave quantum processing unit
print("Running code for D-Wave:\n")
print("from dwave.system import DWaveSampler, EmbeddingComposite")
print("sampler_auto = EmbeddingComposite(DWaveSampler(solver={'qpu': True}))\n")
print("linear = {", end = "")
for i in range(qubits*Dimension-1): 
    linear = i + 1
    print ("('q",linear,"','q",linear,"'):",format(QM[i][i]),sep='', end = ", ")
print ("('q",qubits*Dimension,"','q",qubits*Dimension,"'):",format(QM[qubits*Dimension-1][qubits*Dimension-1]),"}", sep='')

print("\nquadratic = {", end = "")
for i in range(qubits*Dimension-1):
    for j in range(i+1,qubits*Dimension):
        if QM[i][j] != 0:
            qdrt1 = i + 1
            qdrt2 = j + 1
            if i == qubits*Dimension-2 and j == qubits*Dimension-1:
                print ("('q",qdrt1,"','q",qdrt2,"'):",format(QM[i][j]), "}", sep='')
            else:
                print ("('q",qdrt1,"','q",qdrt2,"'):",format(QM[i][j]), sep ='', end = ", ")

print("\nQ = dict(linear)")
print("Q.update(quadratic)\n")

qa_iter = 1000
print("sampleset = sampler_auto.sample_qubo(Q, num_reads=",qa_iter,")", sep = "")
print("print(sampleset)")      

# Matrix Q is
[[-7.8640e+03  3.3520e+03  4.6000e+02  9.2000e+02 -6.3000e+02 -1.2600e+03
  -3.0000e+01 -6.0000e+01 -2.4000e+01 -4.8000e+01  2.7800e+02  5.5600e+02
   7.1800e+02  1.4360e+03  3.4000e+01  6.8000e+01  4.0600e+02  8.1200e+02
   3.8200e+02  7.6400e+02  4.3400e+02  8.6800e+02  2.5000e+02  5.0000e+02
  -3.2000e+02 -6.4000e+02  1.1000e+02  2.2000e+02 -6.4000e+01 -1.2800e+02
  -2.5000e+02 -5.0000e+02  3.3600e+02  6.7200e+02  1.4000e+02  2.8000e+02
   4.5800e+02  9.1600e+02 -2.4000e+01 -4.8000e+01  7.7400e+02  1.5480e+03
  -3.8400e+02 -7.6800e+02  4.8600e+02  9.7200e+02  2.5400e+02  5.0800e+02
  -2.5600e+02 -5.1200e+02  2.1000e+02  4.2000e+02 -3.9800e+02 -7.9600e+02
   9.4000e+01  1.8800e+02  6.0000e+01  1.2000e+02  2.7800e+02  5.5600e+02
   4.1200e+02  8.2400e+02  4.8000e+02  9.6000e+02]
 [ 0.0000e+00 -1.4052e+04  9.2000e+02  1.8400e+03 -1.2600e+03 -2.5200e+03
  -6.0000e+01 -1.2000e+02 -4.8000e+01 -9.6000e+01  5.5600e+02  1.1120e+03
   1.4360e+03  2.8720e+03  6.8000e+01  1.3600e+

quadratic = {('q1','q2'):3352.0, ('q1','q3'):460.0, ('q1','q4'):920.0, ('q1','q5'):-630.0, ('q1','q6'):-1260.0, ('q1','q7'):-30.0, ('q1','q8'):-60.0, ('q1','q9'):-24.0, ('q1','q10'):-48.0, ('q1','q11'):278.0, ('q1','q12'):556.0, ('q1','q13'):718.0, ('q1','q14'):1436.0, ('q1','q15'):34.0, ('q1','q16'):68.0, ('q1','q17'):406.0, ('q1','q18'):812.0, ('q1','q19'):382.0, ('q1','q20'):764.0, ('q1','q21'):434.0, ('q1','q22'):868.0, ('q1','q23'):250.0, ('q1','q24'):500.0, ('q1','q25'):-320.0, ('q1','q26'):-640.0, ('q1','q27'):110.0, ('q1','q28'):220.0, ('q1','q29'):-64.0, ('q1','q30'):-128.0, ('q1','q31'):-250.0, ('q1','q32'):-500.0, ('q1','q33'):336.0, ('q1','q34'):672.0, ('q1','q35'):140.0, ('q1','q36'):280.0, ('q1','q37'):458.0, ('q1','q38'):916.0, ('q1','q39'):-24.0, ('q1','q40'):-48.0, ('q1','q41'):774.0, ('q1','q42'):1548.0, ('q1','q43'):-384.0, ('q1','q44'):-768.0, ('q1','q45'):486.0, ('q1','q46'):972.0, ('q1','q47'):254.0, ('q1','q48'):508.0, ('q1','q49'):-256.0, ('q1','q50'):-512.0, ('

','q63'):-84.0, ('q27','q64'):-168.0, ('q28','q29'):-888.0, ('q28','q30'):-1776.0, ('q28','q31'):-480.0, ('q28','q32'):-960.0, ('q28','q33'):72.0, ('q28','q34'):144.0, ('q28','q35'):100.0, ('q28','q36'):200.0, ('q28','q37'):-256.0, ('q28','q38'):-512.0, ('q28','q39'):456.0, ('q28','q40'):912.0, ('q28','q41'):308.0, ('q28','q42'):616.0, ('q28','q43'):340.0, ('q28','q44'):680.0, ('q28','q45'):-540.0, ('q28','q46'):-1080.0, ('q28','q47'):408.0, ('q28','q48'):816.0, ('q28','q49'):596.0, ('q28','q50'):1192.0, ('q28','q51'):-172.0, ('q28','q52'):-344.0, ('q28','q53'):112.0, ('q28','q54'):224.0, ('q28','q55'):108.0, ('q28','q56'):216.0, ('q28','q57'):28.0, ('q28','q58'):56.0, ('q28','q59'):-548.0, ('q28','q60'):-1096.0, ('q28','q61'):172.0, ('q28','q62'):344.0, ('q28','q63'):-168.0, ('q28','q64'):-336.0, ('q29','q30'):4812.0, ('q29','q31'):-622.0, ('q29','q32'):-1244.0, ('q29','q33'):-428.0, ('q29','q34'):-856.0, ('q29','q35'):8.0, ('q29','q36'):16.0, ('q29','q37'):284.0, ('q29','q38'):568.0,

In [7]:
from dwave.system import DWaveSampler, EmbeddingComposite
sampler_auto = EmbeddingComposite(DWaveSampler(solver={'qpu': True}))

linear = {('q1','q1'):-7864.0, ('q2','q2'):-14052.0, ('q3','q3'):-6590.0, ('q4','q4'):-10824.0, ('q5','q5'):-6578.0, ('q6','q6'):-10972.0, ('q7','q7'):-2051.0, ('q8','q8'):-2100.0, ('q9','q9'):493.0, ('q10','q10'):3772.0, ('q11','q11'):-819.0, ('q12','q12'):692.0, ('q13','q13'):-15401.0, ('q14','q14'):-28328.0, ('q15','q15'):-3541.0, ('q16','q16'):-4980.0, ('q17','q17'):1302.0, ('q18','q18'):4760.0, ('q19','q19'):-5806.0, ('q20','q20'):-8672.0, ('q21','q21'):-9846.0, ('q22','q22'):-17564.0, ('q23','q23'):-8106.0, ('q24','q24'):-14248.0, ('q25','q25'):341.0, ('q26','q26'):2252.0, ('q27','q27'):-2970.0, ('q28','q28'):-3816.0, ('q29','q29'):419.0, ('q30','q30'):3244.0, ('q31','q31'):-4604.0, ('q32','q32'):-6500.0, ('q33','q33'):-8520.0, ('q34','q34'):-14052.0, ('q35','q35'):-1145.0, ('q36','q36'):-604.0, ('q37','q37'):-9609.0, ('q38','q38'):-16840.0, ('q39','q39'):-8757.0, ('q40','q40'):-15496.0, ('q41','q41'):-5580.0, ('q42','q42'):-8376.0, ('q43','q43'):-2764.0, ('q44','q44'):-3740.0, ('q45','q45'):-583.0, ('q46','q46'):864.0, ('q47','q47'):-8591.0, ('q48','q48'):-15200.0, ('q49','q49'):-3806.0, ('q50','q50'):-5500.0, ('q51','q51'):-5355.0, ('q52','q52'):-8408.0, ('q53','q53'):-8859.0, ('q54','q54'):-15348.0, ('q55','q55'):2576.0, ('q56','q56'):6824.0, ('q57','q57'):1927.0, ('q58','q58'):5964.0, ('q59','q59'):-3926.0, ('q60','q60'):-6252.0, ('q61','q61'):-5061.0, ('q62','q62'):-8692.0, ('q63','q63'):-2609.0, ('q64','q64'):-2664.0}

quadratic = {('q1','q2'):3352.0, ('q1','q3'):460.0, ('q1','q4'):920.0, ('q1','q5'):-630.0, ('q1','q6'):-1260.0, ('q1','q7'):-30.0, ('q1','q8'):-60.0, ('q1','q9'):-24.0, ('q1','q10'):-48.0, ('q1','q11'):278.0, ('q1','q12'):556.0, ('q1','q13'):718.0, ('q1','q14'):1436.0, ('q1','q15'):34.0, ('q1','q16'):68.0, ('q1','q17'):406.0, ('q1','q18'):812.0, ('q1','q19'):382.0, ('q1','q20'):764.0, ('q1','q21'):434.0, ('q1','q22'):868.0, ('q1','q23'):250.0, ('q1','q24'):500.0, ('q1','q25'):-320.0, ('q1','q26'):-640.0, ('q1','q27'):110.0, ('q1','q28'):220.0, ('q1','q29'):-64.0, ('q1','q30'):-128.0, ('q1','q31'):-250.0, ('q1','q32'):-500.0, ('q1','q33'):336.0, ('q1','q34'):672.0, ('q1','q35'):140.0, ('q1','q36'):280.0, ('q1','q37'):458.0, ('q1','q38'):916.0, ('q1','q39'):-24.0, ('q1','q40'):-48.0, ('q1','q41'):774.0, ('q1','q42'):1548.0, ('q1','q43'):-384.0, ('q1','q44'):-768.0, ('q1','q45'):486.0, ('q1','q46'):972.0, ('q1','q47'):254.0, ('q1','q48'):508.0, ('q1','q49'):-256.0, ('q1','q50'):-512.0, ('q1','q51'):210.0, ('q1','q52'):420.0, ('q1','q53'):-398.0, ('q1','q54'):-796.0, ('q1','q55'):94.0, ('q1','q56'):188.0, ('q1','q57'):60.0, ('q1','q58'):120.0, ('q1','q59'):278.0, ('q1','q60'):556.0, ('q1','q61'):412.0, ('q1','q62'):824.0, ('q1','q63'):480.0, ('q1','q64'):960.0, ('q2','q3'):920.0, ('q2','q4'):1840.0, ('q2','q5'):-1260.0, ('q2','q6'):-2520.0, ('q2','q7'):-60.0, ('q2','q8'):-120.0, ('q2','q9'):-48.0, ('q2','q10'):-96.0, ('q2','q11'):556.0, ('q2','q12'):1112.0, ('q2','q13'):1436.0, ('q2','q14'):2872.0, ('q2','q15'):68.0, ('q2','q16'):136.0, ('q2','q17'):812.0, ('q2','q18'):1624.0, ('q2','q19'):764.0, ('q2','q20'):1528.0, ('q2','q21'):868.0, ('q2','q22'):1736.0, ('q2','q23'):500.0, ('q2','q24'):1000.0, ('q2','q25'):-640.0, ('q2','q26'):-1280.0, ('q2','q27'):220.0, ('q2','q28'):440.0, ('q2','q29'):-128.0, ('q2','q30'):-256.0, ('q2','q31'):-500.0, ('q2','q32'):-1000.0, ('q2','q33'):672.0, ('q2','q34'):1344.0, ('q2','q35'):280.0, ('q2','q36'):560.0, ('q2','q37'):916.0, ('q2','q38'):1832.0, ('q2','q39'):-48.0, ('q2','q40'):-96.0, ('q2','q41'):1548.0, ('q2','q42'):3096.0, ('q2','q43'):-768.0, ('q2','q44'):-1536.0, ('q2','q45'):972.0, ('q2','q46'):1944.0, ('q2','q47'):508.0, ('q2','q48'):1016.0, ('q2','q49'):-512.0, ('q2','q50'):-1024.0, ('q2','q51'):420.0, ('q2','q52'):840.0, ('q2','q53'):-796.0, ('q2','q54'):-1592.0, ('q2','q55'):188.0, ('q2','q56'):376.0, ('q2','q57'):120.0, ('q2','q58'):240.0, ('q2','q59'):556.0, ('q2','q60'):1112.0, ('q2','q61'):824.0, ('q2','q62'):1648.0, ('q2','q63'):960.0, ('q2','q64'):1920.0, ('q3','q4'):4712.0, ('q3','q5'):-60.0, ('q3','q6'):-120.0, ('q3','q7'):-138.0, ('q3','q8'):-276.0, ('q3','q9'):194.0, ('q3','q10'):388.0, ('q3','q11'):-78.0, ('q3','q12'):-156.0, ('q3','q13'):582.0, ('q3','q14'):1164.0, ('q3','q15'):-406.0, ('q3','q16'):-812.0, ('q3','q17'):-170.0, ('q3','q18'):-340.0, ('q3','q19'):238.0, ('q3','q20'):476.0, ('q3','q21'):108.0, ('q3','q22'):216.0, ('q3','q23'):394.0, ('q3','q24'):788.0, ('q3','q25'):52.0, ('q3','q26'):104.0, ('q3','q27'):-274.0, ('q3','q28'):-548.0, ('q3','q29'):-374.0, ('q3','q30'):-748.0, ('q3','q31'):1330.0, ('q3','q32'):2660.0, ('q3','q33'):334.0, ('q3','q34'):668.0, ('q3','q35'):744.0, ('q3','q36'):1488.0, ('q3','q37'):296.0, ('q3','q38'):592.0, ('q3','q39'):130.0, ('q3','q40'):260.0, ('q3','q41'):354.0, ('q3','q42'):708.0, ('q3','q43'):-222.0, ('q3','q44'):-444.0, ('q3','q45'):234.0, ('q3','q46'):468.0, ('q3','q47'):384.0, ('q3','q48'):768.0, ('q3','q49'):-532.0, ('q3','q50'):-1064.0, ('q3','q51'):-12.0, ('q3','q52'):-24.0, ('q3','q53'):-294.0, ('q3','q54'):-588.0, ('q3','q55'):-540.0, ('q3','q56'):-1080.0, ('q3','q57'):-674.0, ('q3','q58'):-1348.0, ('q3','q59'):590.0, ('q3','q60'):1180.0, ('q3','q61'):248.0, ('q3','q62'):496.0, ('q3','q63'):-188.0, ('q3','q64'):-376.0, ('q4','q5'):-120.0, ('q4','q6'):-240.0, ('q4','q7'):-276.0, ('q4','q8'):-552.0, ('q4','q9'):388.0, ('q4','q10'):776.0, ('q4','q11'):-156.0, ('q4','q12'):-312.0, ('q4','q13'):1164.0, ('q4','q14'):2328.0, ('q4','q15'):-812.0, ('q4','q16'):-1624.0, ('q4','q17'):-340.0, ('q4','q18'):-680.0, ('q4','q19'):476.0, ('q4','q20'):952.0, ('q4','q21'):216.0, ('q4','q22'):432.0, ('q4','q23'):788.0, ('q4','q24'):1576.0, ('q4','q25'):104.0, ('q4','q26'):208.0, ('q4','q27'):-548.0, ('q4','q28'):-1096.0, ('q4','q29'):-748.0, ('q4','q30'):-1496.0, ('q4','q31'):2660.0, ('q4','q32'):5320.0, ('q4','q33'):668.0, ('q4','q34'):1336.0, ('q4','q35'):1488.0, ('q4','q36'):2976.0, ('q4','q37'):592.0, ('q4','q38'):1184.0, ('q4','q39'):260.0, ('q4','q40'):520.0, ('q4','q41'):708.0, ('q4','q42'):1416.0, ('q4','q43'):-444.0, ('q4','q44'):-888.0, ('q4','q45'):468.0, ('q4','q46'):936.0, ('q4','q47'):768.0, ('q4','q48'):1536.0, ('q4','q49'):-1064.0, ('q4','q50'):-2128.0, ('q4','q51'):-24.0, ('q4','q52'):-48.0, ('q4','q53'):-588.0, ('q4','q54'):-1176.0, ('q4','q55'):-1080.0, ('q4','q56'):-2160.0, ('q4','q57'):-1348.0, ('q4','q58'):-2696.0, ('q4','q59'):1180.0, ('q4','q60'):2360.0, ('q4','q61'):496.0, ('q4','q62'):992.0, ('q4','q63'):-376.0, ('q4','q64'):-752.0, ('q5','q6'):4368.0, ('q5','q7'):-126.0, ('q5','q8'):-252.0, ('q5','q9'):-680.0, ('q5','q10'):-1360.0, ('q5','q11'):-428.0, ('q5','q12'):-856.0, ('q5','q13'):82.0, ('q5','q14'):164.0, ('q5','q15'):444.0, ('q5','q16'):888.0, ('q5','q17'):84.0, ('q5','q18'):168.0, ('q5','q19'):-284.0, ('q5','q20'):-568.0, ('q5','q21'):-106.0, ('q5','q22'):-212.0, ('q5','q23'):-8.0, ('q5','q24'):-16.0, ('q5','q25'):150.0, ('q5','q26'):300.0, ('q5','q27'):-236.0, ('q5','q28'):-472.0, ('q5','q29'):180.0, ('q5','q30'):360.0, ('q5','q31'):594.0, ('q5','q32'):1188.0, ('q5','q33'):518.0, ('q5','q34'):1036.0, ('q5','q35'):146.0, ('q5','q36'):292.0, ('q5','q37'):406.0, ('q5','q38'):812.0, ('q5','q39'):110.0, ('q5','q40'):220.0, ('q5','q41'):240.0, ('q5','q42'):480.0, ('q5','q43'):852.0, ('q5','q44'):1704.0, ('q5','q45'):-978.0, ('q5','q46'):-1956.0, ('q5','q47'):188.0, ('q5','q48'):376.0, ('q5','q49'):-6.0, ('q5','q50'):-12.0, ('q5','q51'):472.0, ('q5','q52'):944.0, ('q5','q53'):542.0, ('q5','q54'):1084.0, ('q5','q55'):-408.0, ('q5','q56'):-816.0, ('q5','q57'):-362.0, ('q5','q58'):-724.0, ('q5','q59'):228.0, ('q5','q60'):456.0, ('q5','q61'):-276.0, ('q5','q62'):-552.0, ('q5','q63'):138.0, ('q5','q64'):276.0, ('q6','q7'):-252.0, ('q6','q8'):-504.0, ('q6','q9'):-1360.0, ('q6','q10'):-2720.0, ('q6','q11'):-856.0, ('q6','q12'):-1712.0, ('q6','q13'):164.0, ('q6','q14'):328.0, ('q6','q15'):888.0, ('q6','q16'):1776.0, ('q6','q17'):168.0, ('q6','q18'):336.0, ('q6','q19'):-568.0, ('q6','q20'):-1136.0, ('q6','q21'):-212.0, ('q6','q22'):-424.0, ('q6','q23'):-16.0, ('q6','q24'):-32.0, ('q6','q25'):300.0, ('q6','q26'):600.0, ('q6','q27'):-472.0, ('q6','q28'):-944.0, ('q6','q29'):360.0, ('q6','q30'):720.0, ('q6','q31'):1188.0, ('q6','q32'):2376.0, ('q6','q33'):1036.0, ('q6','q34'):2072.0, ('q6','q35'):292.0, ('q6','q36'):584.0, ('q6','q37'):812.0, ('q6','q38'):1624.0, ('q6','q39'):220.0, ('q6','q40'):440.0, ('q6','q41'):480.0, ('q6','q42'):960.0, ('q6','q43'):1704.0, ('q6','q44'):3408.0, ('q6','q45'):-1956.0, ('q6','q46'):-3912.0, ('q6','q47'):376.0, ('q6','q48'):752.0, ('q6','q49'):-12.0, ('q6','q50'):-24.0, ('q6','q51'):944.0, ('q6','q52'):1888.0, ('q6','q53'):1084.0, ('q6','q54'):2168.0, ('q6','q55'):-816.0, ('q6','q56'):-1632.0, ('q6','q57'):-724.0, ('q6','q58'):-1448.0, ('q6','q59'):456.0, ('q6','q60'):912.0, ('q6','q61'):-552.0, ('q6','q62'):-1104.0, ('q6','q63'):276.0, ('q6','q64'):552.0, ('q7','q8'):4004.0, ('q7','q9'):-218.0, ('q7','q10'):-436.0, ('q7','q11'):342.0, ('q7','q12'):684.0, ('q7','q13'):588.0, ('q7','q14'):1176.0, ('q7','q15'):106.0, ('q7','q16'):212.0, ('q7','q17'):138.0, ('q7','q18'):276.0, ('q7','q19'):-530.0, ('q7','q20'):-1060.0, ('q7','q21'):-52.0, ('q7','q22'):-104.0, ('q7','q23'):154.0, ('q7','q24'):308.0, ('q7','q25'):-120.0, ('q7','q26'):-240.0, ('q7','q27'):-92.0, ('q7','q28'):-184.0, ('q7','q29'):394.0, ('q7','q30'):788.0, ('q7','q31'):-28.0, ('q7','q32'):-56.0, ('q7','q33'):104.0, ('q7','q34'):208.0, ('q7','q35'):410.0, ('q7','q36'):820.0, ('q7','q37'):-64.0, ('q7','q38'):-128.0, ('q7','q39'):-436.0, ('q7','q40'):-872.0, ('q7','q41'):-286.0, ('q7','q42'):-572.0, ('q7','q43'):-568.0, ('q7','q44'):-1136.0, ('q7','q45'):-332.0, ('q7','q46'):-664.0, ('q7','q47'):26.0, ('q7','q48'):52.0, ('q7','q49'):146.0, ('q7','q50'):292.0, ('q7','q51'):608.0, ('q7','q52'):1216.0, ('q7','q53'):-422.0, ('q7','q54'):-844.0, ('q7','q55'):-236.0, ('q7','q56'):-472.0, ('q7','q57'):-584.0, ('q7','q58'):-1168.0, ('q7','q59'):-646.0, ('q7','q60'):-1292.0, ('q7','q61'):52.0, ('q7','q62'):104.0, ('q7','q63'):-72.0, ('q7','q64'):-144.0, ('q8','q9'):-436.0, ('q8','q10'):-872.0, ('q8','q11'):684.0, ('q8','q12'):1368.0, ('q8','q13'):1176.0, ('q8','q14'):2352.0, ('q8','q15'):212.0, ('q8','q16'):424.0, ('q8','q17'):276.0, ('q8','q18'):552.0, ('q8','q19'):-1060.0, ('q8','q20'):-2120.0, ('q8','q21'):-104.0, ('q8','q22'):-208.0, ('q8','q23'):308.0, ('q8','q24'):616.0, ('q8','q25'):-240.0, ('q8','q26'):-480.0, ('q8','q27'):-184.0, ('q8','q28'):-368.0, ('q8','q29'):788.0, ('q8','q30'):1576.0, ('q8','q31'):-56.0, ('q8','q32'):-112.0, ('q8','q33'):208.0, ('q8','q34'):416.0, ('q8','q35'):820.0, ('q8','q36'):1640.0, ('q8','q37'):-128.0, ('q8','q38'):-256.0, ('q8','q39'):-872.0, ('q8','q40'):-1744.0, ('q8','q41'):-572.0, ('q8','q42'):-1144.0, ('q8','q43'):-1136.0, ('q8','q44'):-2272.0, ('q8','q45'):-664.0, ('q8','q46'):-1328.0, ('q8','q47'):52.0, ('q8','q48'):104.0, ('q8','q49'):292.0, ('q8','q50'):584.0, ('q8','q51'):1216.0, ('q8','q52'):2432.0, ('q8','q53'):-844.0, ('q8','q54'):-1688.0, ('q8','q55'):-472.0, ('q8','q56'):-944.0, ('q8','q57'):-1168.0, ('q8','q58'):-2336.0, ('q8','q59'):-1292.0, ('q8','q60'):-2584.0, ('q8','q61'):104.0, ('q8','q62'):208.0, ('q8','q63'):-144.0, ('q8','q64'):-288.0, ('q9','q10'):5572.0, ('q9','q11'):-352.0, ('q9','q12'):-704.0, ('q9','q13'):-50.0, ('q9','q14'):-100.0, ('q9','q15'):98.0, ('q9','q16'):196.0, ('q9','q17'):-400.0, ('q9','q18'):-800.0, ('q9','q19'):928.0, ('q9','q20'):1856.0, ('q9','q21'):396.0, ('q9','q22'):792.0, ('q9','q23'):122.0, ('q9','q24'):244.0, ('q9','q25'):394.0, ('q9','q26'):788.0, ('q9','q27'):152.0, ('q9','q28'):304.0, ('q9','q29'):576.0, ('q9','q30'):1152.0, ('q9','q31'):-404.0, ('q9','q32'):-808.0, ('q9','q33'):-434.0, ('q9','q34'):-868.0, ('q9','q35'):432.0, ('q9','q36'):864.0, ('q9','q37'):-464.0, ('q9','q38'):-928.0, ('q9','q39'):564.0, ('q9','q40'):1128.0, ('q9','q41'):-338.0, ('q9','q42'):-676.0, ('q9','q43'):320.0, ('q9','q44'):640.0, ('q9','q45'):200.0, ('q9','q46'):400.0, ('q9','q47'):364.0, ('q9','q48'):728.0, ('q9','q49'):336.0, ('q9','q50'):672.0, ('q9','q51'):-184.0, ('q9','q52'):-368.0, ('q9','q53'):150.0, ('q9','q54'):300.0, ('q9','q55'):712.0, ('q9','q56'):1424.0, ('q9','q57'):-664.0, ('q9','q58'):-1328.0, ('q9','q59'):74.0, ('q9','q60'):148.0, ('q9','q61'):230.0, ('q9','q62'):460.0, ('q9','q63'):-118.0, ('q9','q64'):-236.0, ('q10','q11'):-704.0, ('q10','q12'):-1408.0, ('q10','q13'):-100.0, ('q10','q14'):-200.0, ('q10','q15'):196.0, ('q10','q16'):392.0, ('q10','q17'):-800.0, ('q10','q18'):-1600.0, ('q10','q19'):1856.0, ('q10','q20'):3712.0, ('q10','q21'):792.0, ('q10','q22'):1584.0, ('q10','q23'):244.0, ('q10','q24'):488.0, ('q10','q25'):788.0, ('q10','q26'):1576.0, ('q10','q27'):304.0, ('q10','q28'):608.0, ('q10','q29'):1152.0, ('q10','q30'):2304.0, ('q10','q31'):-808.0, ('q10','q32'):-1616.0, ('q10','q33'):-868.0, ('q10','q34'):-1736.0, ('q10','q35'):864.0, ('q10','q36'):1728.0, ('q10','q37'):-928.0, ('q10','q38'):-1856.0, ('q10','q39'):1128.0, ('q10','q40'):2256.0, ('q10','q41'):-676.0, ('q10','q42'):-1352.0, ('q10','q43'):640.0, ('q10','q44'):1280.0, ('q10','q45'):400.0, ('q10','q46'):800.0, ('q10','q47'):728.0, ('q10','q48'):1456.0, ('q10','q49'):672.0, ('q10','q50'):1344.0, ('q10','q51'):-368.0, ('q10','q52'):-736.0, ('q10','q53'):300.0, ('q10','q54'):600.0, ('q10','q55'):1424.0, ('q10','q56'):2848.0, ('q10','q57'):-1328.0, ('q10','q58'):-2656.0, ('q10','q59'):148.0, ('q10','q60'):296.0, ('q10','q61'):460.0, ('q10','q62'):920.0, ('q10','q63'):-236.0, ('q10','q64'):-472.0, ('q11','q12'):4660.0, ('q11','q13'):108.0, ('q11','q14'):216.0, ('q11','q15'):-290.0, ('q11','q16'):-580.0, ('q11','q17'):550.0, ('q11','q18'):1100.0, ('q11','q19'):278.0, ('q11','q20'):556.0, ('q11','q21'):76.0, ('q11','q22'):152.0, ('q11','q23'):68.0, ('q11','q24'):136.0, ('q11','q25'):296.0, ('q11','q26'):592.0, ('q11','q27'):-466.0, ('q11','q28'):-932.0, ('q11','q29'):-122.0, ('q11','q30'):-244.0, ('q11','q31'):-180.0, ('q11','q32'):-360.0, ('q11','q33'):-200.0, ('q11','q34'):-400.0, ('q11','q35'):-294.0, ('q11','q36'):-588.0, ('q11','q37'):204.0, ('q11','q38'):408.0, ('q11','q39'):-102.0, ('q11','q40'):-204.0, ('q11','q41'):180.0, ('q11','q42'):360.0, ('q11','q43'):82.0, ('q11','q44'):164.0, ('q11','q45'):68.0, ('q11','q46'):136.0, ('q11','q47'):-700.0, ('q11','q48'):-1400.0, ('q11','q49'):-626.0, ('q11','q50'):-1252.0, ('q11','q51'):110.0, ('q11','q52'):220.0, ('q11','q53'):-40.0, ('q11','q54'):-80.0, ('q11','q55'):156.0, ('q11','q56'):312.0, ('q11','q57'):124.0, ('q11','q58'):248.0, ('q11','q59'):-104.0, ('q11','q60'):-208.0, ('q11','q61'):136.0, ('q11','q62'):272.0, ('q11','q63'):-6.0, ('q11','q64'):-12.0, ('q12','q13'):216.0, ('q12','q14'):432.0, ('q12','q15'):-580.0, ('q12','q16'):-1160.0, ('q12','q17'):1100.0, ('q12','q18'):2200.0, ('q12','q19'):556.0, ('q12','q20'):1112.0, ('q12','q21'):152.0, ('q12','q22'):304.0, ('q12','q23'):136.0, ('q12','q24'):272.0, ('q12','q25'):592.0, ('q12','q26'):1184.0, ('q12','q27'):-932.0, ('q12','q28'):-1864.0, ('q12','q29'):-244.0, ('q12','q30'):-488.0, ('q12','q31'):-360.0, ('q12','q32'):-720.0, ('q12','q33'):-400.0, ('q12','q34'):-800.0, ('q12','q35'):-588.0, ('q12','q36'):-1176.0, ('q12','q37'):408.0, ('q12','q38'):816.0, ('q12','q39'):-204.0, ('q12','q40'):-408.0, ('q12','q41'):360.0, ('q12','q42'):720.0, ('q12','q43'):164.0, ('q12','q44'):328.0, ('q12','q45'):136.0, ('q12','q46'):272.0, ('q12','q47'):-1400.0, ('q12','q48'):-2800.0, ('q12','q49'):-1252.0, ('q12','q50'):-2504.0, ('q12','q51'):220.0, ('q12','q52'):440.0, ('q12','q53'):-80.0, ('q12','q54'):-160.0, ('q12','q55'):312.0, ('q12','q56'):624.0, ('q12','q57'):248.0, ('q12','q58'):496.0, ('q12','q59'):-208.0, ('q12','q60'):-416.0, ('q12','q61'):272.0, ('q12','q62'):544.0, ('q12','q63'):-12.0, ('q12','q64'):-24.0, ('q13','q14'):4948.0, ('q13','q15'):132.0, ('q13','q16'):264.0, ('q13','q17'):-358.0, ('q13','q18'):-716.0, ('q13','q19'):32.0, ('q13','q20'):64.0, ('q13','q21'):818.0, ('q13','q22'):1636.0, ('q13','q23'):320.0, ('q13','q24'):640.0, ('q13','q25'):-228.0, ('q13','q26'):-456.0, ('q13','q27'):286.0, ('q13','q28'):572.0, ('q13','q29'):-208.0, ('q13','q30'):-416.0, ('q13','q31'):834.0, ('q13','q32'):1668.0, ('q13','q33'):188.0, ('q13','q34'):376.0, ('q13','q35'):-344.0, ('q13','q36'):-688.0, ('q13','q37'):56.0, ('q13','q38'):112.0, ('q13','q39'):-12.0, ('q13','q40'):-24.0, ('q13','q41'):334.0, ('q13','q42'):668.0, ('q13','q43'):-130.0, ('q13','q44'):-260.0, ('q13','q45'):212.0, ('q13','q46'):424.0, ('q13','q47'):528.0, ('q13','q48'):1056.0, ('q13','q49'):246.0, ('q13','q50'):492.0, ('q13','q51'):258.0, ('q13','q52'):516.0, ('q13','q53'):-182.0, ('q13','q54'):-364.0, ('q13','q55'):-150.0, ('q13','q56'):-300.0, ('q13','q57'):-58.0, ('q13','q58'):-116.0, ('q13','q59'):18.0, ('q13','q60'):36.0, ('q13','q61'):136.0, ('q13','q62'):272.0, ('q13','q63'):-178.0, ('q13','q64'):-356.0, ('q14','q15'):264.0, ('q14','q16'):528.0, ('q14','q17'):-716.0, ('q14','q18'):-1432.0, ('q14','q19'):64.0, ('q14','q20'):128.0, ('q14','q21'):1636.0, ('q14','q22'):3272.0, ('q14','q23'):640.0, ('q14','q24'):1280.0, ('q14','q25'):-456.0, ('q14','q26'):-912.0, ('q14','q27'):572.0, ('q14','q28'):1144.0, ('q14','q29'):-416.0, ('q14','q30'):-832.0, ('q14','q31'):1668.0, ('q14','q32'):3336.0, ('q14','q33'):376.0, ('q14','q34'):752.0, ('q14','q35'):-688.0, ('q14','q36'):-1376.0, ('q14','q37'):112.0, ('q14','q38'):224.0, ('q14','q39'):-24.0, ('q14','q40'):-48.0, ('q14','q41'):668.0, ('q14','q42'):1336.0, ('q14','q43'):-260.0, ('q14','q44'):-520.0, ('q14','q45'):424.0, ('q14','q46'):848.0, ('q14','q47'):1056.0, ('q14','q48'):2112.0, ('q14','q49'):492.0, ('q14','q50'):984.0, ('q14','q51'):516.0, ('q14','q52'):1032.0, ('q14','q53'):-364.0, ('q14','q54'):-728.0, ('q14','q55'):-300.0, ('q14','q56'):-600.0, ('q14','q57'):-116.0, ('q14','q58'):-232.0, ('q14','q59'):36.0, ('q14','q60'):72.0, ('q14','q61'):272.0, ('q14','q62'):544.0, ('q14','q63'):-356.0, ('q14','q64'):-712.0, ('q15','q16'):4204.0, ('q15','q17'):82.0, ('q15','q18'):164.0, ('q15','q19'):884.0, ('q15','q20'):1768.0, ('q15','q21'):-308.0, ('q15','q22'):-616.0, ('q15','q23'):504.0, ('q15','q24'):1008.0, ('q15','q25'):-284.0, ('q15','q26'):-568.0, ('q15','q27'):-72.0, ('q15','q28'):-144.0, ('q15','q29'):214.0, ('q15','q30'):428.0, ('q15','q31'):-262.0, ('q15','q32'):-524.0, ('q15','q33'):-416.0, ('q15','q34'):-832.0, ('q15','q35'):400.0, ('q15','q36'):800.0, ('q15','q37'):258.0, ('q15','q38'):516.0, ('q15','q39'):496.0, ('q15','q40'):992.0, ('q15','q41'):-76.0, ('q15','q42'):-152.0, ('q15','q43'):226.0, ('q15','q44'):452.0, ('q15','q45'):-322.0, ('q15','q46'):-644.0, ('q15','q47'):504.0, ('q15','q48'):1008.0, ('q15','q49'):614.0, ('q15','q50'):1228.0, ('q15','q51'):16.0, ('q15','q52'):32.0, ('q15','q53'):212.0, ('q15','q54'):424.0, ('q15','q55'):304.0, ('q15','q56'):608.0, ('q15','q57'):-432.0, ('q15','q58'):-864.0, ('q15','q59'):498.0, ('q15','q60'):996.0, ('q15','q61'):-108.0, ('q15','q62'):-216.0, ('q15','q63'):176.0, ('q15','q64'):352.0, ('q16','q17'):164.0, ('q16','q18'):328.0, ('q16','q19'):1768.0, ('q16','q20'):3536.0, ('q16','q21'):-616.0, ('q16','q22'):-1232.0, ('q16','q23'):1008.0, ('q16','q24'):2016.0, ('q16','q25'):-568.0, ('q16','q26'):-1136.0, ('q16','q27'):-144.0, ('q16','q28'):-288.0, ('q16','q29'):428.0, ('q16','q30'):856.0, ('q16','q31'):-524.0, ('q16','q32'):-1048.0, ('q16','q33'):-832.0, ('q16','q34'):-1664.0, ('q16','q35'):800.0, ('q16','q36'):1600.0, ('q16','q37'):516.0, ('q16','q38'):1032.0, ('q16','q39'):992.0, ('q16','q40'):1984.0, ('q16','q41'):-152.0, ('q16','q42'):-304.0, ('q16','q43'):452.0, ('q16','q44'):904.0, ('q16','q45'):-644.0, ('q16','q46'):-1288.0, ('q16','q47'):1008.0, ('q16','q48'):2016.0, ('q16','q49'):1228.0, ('q16','q50'):2456.0, ('q16','q51'):32.0, ('q16','q52'):64.0, ('q16','q53'):424.0, ('q16','q54'):848.0, ('q16','q55'):608.0, ('q16','q56'):1216.0, ('q16','q57'):-864.0, ('q16','q58'):-1728.0, ('q16','q59'):996.0, ('q16','q60'):1992.0, ('q16','q61'):-216.0, ('q16','q62'):-432.0, ('q16','q63'):352.0, ('q16','q64'):704.0, ('q17','q18'):4312.0, ('q17','q19'):-302.0, ('q17','q20'):-604.0, ('q17','q21'):930.0, ('q17','q22'):1860.0, ('q17','q23'):-594.0, ('q17','q24'):-1188.0, ('q17','q25'):158.0, ('q17','q26'):316.0, ('q17','q27'):-230.0, ('q17','q28'):-460.0, ('q17','q29'):-252.0, ('q17','q30'):-504.0, ('q17','q31'):-222.0, ('q17','q32'):-444.0, ('q17','q33'):-156.0, ('q17','q34'):-312.0, ('q17','q35'):372.0, ('q17','q36'):744.0, ('q17','q37'):-240.0, ('q17','q38'):-480.0, ('q17','q39'):-84.0, ('q17','q40'):-168.0, ('q17','q41'):998.0, ('q17','q42'):1996.0, ('q17','q43'):-132.0, ('q17','q44'):-264.0, ('q17','q45'):-392.0, ('q17','q46'):-784.0, ('q17','q47'):-192.0, ('q17','q48'):-384.0, ('q17','q49'):-226.0, ('q17','q50'):-452.0, ('q17','q51'):212.0, ('q17','q52'):424.0, ('q17','q53'):-314.0, ('q17','q54'):-628.0, ('q17','q55'):450.0, ('q17','q56'):900.0, ('q17','q57'):228.0, ('q17','q58'):456.0, ('q17','q59'):246.0, ('q17','q60'):492.0, ('q17','q61'):98.0, ('q17','q62'):196.0, ('q17','q63'):-422.0, ('q17','q64'):-844.0, ('q18','q19'):-604.0, ('q18','q20'):-1208.0, ('q18','q21'):1860.0, ('q18','q22'):3720.0, ('q18','q23'):-1188.0, ('q18','q24'):-2376.0, ('q18','q25'):316.0, ('q18','q26'):632.0, ('q18','q27'):-460.0, ('q18','q28'):-920.0, ('q18','q29'):-504.0, ('q18','q30'):-1008.0, ('q18','q31'):-444.0, ('q18','q32'):-888.0, ('q18','q33'):-312.0, ('q18','q34'):-624.0, ('q18','q35'):744.0, ('q18','q36'):1488.0, ('q18','q37'):-480.0, ('q18','q38'):-960.0, ('q18','q39'):-168.0, ('q18','q40'):-336.0, ('q18','q41'):1996.0, ('q18','q42'):3992.0, ('q18','q43'):-264.0, ('q18','q44'):-528.0, ('q18','q45'):-784.0, ('q18','q46'):-1568.0, ('q18','q47'):-384.0, ('q18','q48'):-768.0, ('q18','q49'):-452.0, ('q18','q50'):-904.0, ('q18','q51'):424.0, ('q18','q52'):848.0, ('q18','q53'):-628.0, ('q18','q54'):-1256.0, ('q18','q55'):900.0, ('q18','q56'):1800.0, ('q18','q57'):456.0, ('q18','q58'):912.0, ('q18','q59'):492.0, ('q18','q60'):984.0, ('q18','q61'):196.0, ('q18','q62'):392.0, ('q18','q63'):-844.0, ('q18','q64'):-1688.0, ('q19','q20'):5880.0, ('q19','q21'):-290.0, ('q19','q22'):-580.0, ('q19','q23'):1136.0, ('q19','q24'):2272.0, ('q19','q25'):-286.0, ('q19','q26'):-572.0, ('q19','q27'):-338.0, ('q19','q28'):-676.0, ('q19','q29'):552.0, ('q19','q30'):1104.0, ('q19','q31'):-840.0, ('q19','q32'):-1680.0, ('q19','q33'):-274.0, ('q19','q34'):-548.0, ('q19','q35'):202.0, ('q19','q36'):404.0, ('q19','q37'):-6.0, ('q19','q38'):-12.0, ('q19','q39'):1246.0, ('q19','q40'):2492.0, ('q19','q41'):154.0, ('q19','q42'):308.0, ('q19','q43'):-46.0, ('q19','q44'):-92.0, ('q19','q45'):-30.0, ('q19','q46'):-60.0, ('q19','q47'):936.0, ('q19','q48'):1872.0, ('q19','q49'):-52.0, ('q19','q50'):-104.0, ('q19','q51'):-774.0, ('q19','q52'):-1548.0, ('q19','q53'):752.0, ('q19','q54'):1504.0, ('q19','q55'):306.0, ('q19','q56'):612.0, ('q19','q57'):-178.0, ('q19','q58'):-356.0, ('q19','q59'):1034.0, ('q19','q60'):2068.0, ('q19','q61'):-98.0, ('q19','q62'):-196.0, ('q19','q63'):-552.0, ('q19','q64'):-1104.0, ('q20','q21'):-580.0, ('q20','q22'):-1160.0, ('q20','q23'):2272.0, ('q20','q24'):4544.0, ('q20','q25'):-572.0, ('q20','q26'):-1144.0, ('q20','q27'):-676.0, ('q20','q28'):-1352.0, ('q20','q29'):1104.0, ('q20','q30'):2208.0, ('q20','q31'):-1680.0, ('q20','q32'):-3360.0, ('q20','q33'):-548.0, ('q20','q34'):-1096.0, ('q20','q35'):404.0, ('q20','q36'):808.0, ('q20','q37'):-12.0, ('q20','q38'):-24.0, ('q20','q39'):2492.0, ('q20','q40'):4984.0, ('q20','q41'):308.0, ('q20','q42'):616.0, ('q20','q43'):-92.0, ('q20','q44'):-184.0, ('q20','q45'):-60.0, ('q20','q46'):-120.0, ('q20','q47'):1872.0, ('q20','q48'):3744.0, ('q20','q49'):-104.0, ('q20','q50'):-208.0, ('q20','q51'):-1548.0, ('q20','q52'):-3096.0, ('q20','q53'):1504.0, ('q20','q54'):3008.0, ('q20','q55'):612.0, ('q20','q56'):1224.0, ('q20','q57'):-356.0, ('q20','q58'):-712.0, ('q20','q59'):2068.0, ('q20','q60'):4136.0, ('q20','q61'):-196.0, ('q20','q62'):-392.0, ('q20','q63'):-1104.0, ('q20','q64'):-2208.0, ('q21','q22'):4256.0, ('q21','q23'):-576.0, ('q21','q24'):-1152.0, ('q21','q25'):-28.0, ('q21','q26'):-56.0, ('q21','q27'):440.0, ('q21','q28'):880.0, ('q21','q29'):2.0, ('q21','q30'):4.0, ('q21','q31'):66.0, ('q21','q32'):132.0, ('q21','q33'):102.0, ('q21','q34'):204.0, ('q21','q35'):-136.0, ('q21','q36'):-272.0, ('q21','q37'):-8.0, ('q21','q38'):-16.0, ('q21','q39'):450.0, ('q21','q40'):900.0, ('q21','q41'):-112.0, ('q21','q42'):-224.0, ('q21','q43'):-78.0, ('q21','q44'):-156.0, ('q21','q45'):342.0, ('q21','q46'):684.0, ('q21','q47'):388.0, ('q21','q48'):776.0, ('q21','q49'):458.0, ('q21','q50'):916.0, ('q21','q51'):-46.0, ('q21','q52'):-92.0, ('q21','q53'):370.0, ('q21','q54'):740.0, ('q21','q55'):436.0, ('q21','q56'):872.0, ('q21','q57'):302.0, ('q21','q58'):604.0, ('q21','q59'):240.0, ('q21','q60'):480.0, ('q21','q61'):662.0, ('q21','q62'):1324.0, ('q21','q63'):-380.0, ('q21','q64'):-760.0, ('q22','q23'):-1152.0, ('q22','q24'):-2304.0, ('q22','q25'):-56.0, ('q22','q26'):-112.0, ('q22','q27'):880.0, ('q22','q28'):1760.0, ('q22','q29'):4.0, ('q22','q30'):8.0, ('q22','q31'):132.0, ('q22','q32'):264.0, ('q22','q33'):204.0, ('q22','q34'):408.0, ('q22','q35'):-272.0, ('q22','q36'):-544.0, ('q22','q37'):-16.0, ('q22','q38'):-32.0, ('q22','q39'):900.0, ('q22','q40'):1800.0, ('q22','q41'):-224.0, ('q22','q42'):-448.0, ('q22','q43'):-156.0, ('q22','q44'):-312.0, ('q22','q45'):684.0, ('q22','q46'):1368.0, ('q22','q47'):776.0, ('q22','q48'):1552.0, ('q22','q49'):916.0, ('q22','q50'):1832.0, ('q22','q51'):-92.0, ('q22','q52'):-184.0, ('q22','q53'):740.0, ('q22','q54'):1480.0, ('q22','q55'):872.0, ('q22','q56'):1744.0, ('q22','q57'):604.0, ('q22','q58'):1208.0, ('q22','q59'):480.0, ('q22','q60'):960.0, ('q22','q61'):1324.0, ('q22','q62'):2648.0, ('q22','q63'):-760.0, ('q22','q64'):-1520.0, ('q23','q24'):3928.0, ('q23','q25'):-222.0, ('q23','q26'):-444.0, ('q23','q27'):-92.0, ('q23','q28'):-184.0, ('q23','q29'):334.0, ('q23','q30'):668.0, ('q23','q31'):-148.0, ('q23','q32'):-296.0, ('q23','q33'):320.0, ('q23','q34'):640.0, ('q23','q35'):30.0, ('q23','q36'):60.0, ('q23','q37'):412.0, ('q23','q38'):824.0, ('q23','q39'):866.0, ('q23','q40'):1732.0, ('q23','q41'):56.0, ('q23','q42'):112.0, ('q23','q43'):316.0, ('q23','q44'):632.0, ('q23','q45'):408.0, ('q23','q46'):816.0, ('q23','q47'):852.0, ('q23','q48'):1704.0, ('q23','q49'):-274.0, ('q23','q50'):-548.0, ('q23','q51'):-424.0, ('q23','q52'):-848.0, ('q23','q53'):138.0, ('q23','q54'):276.0, ('q23','q55'):-28.0, ('q23','q56'):-56.0, ('q23','q57'):-570.0, ('q23','q58'):-1140.0, ('q23','q59'):362.0, ('q23','q60'):724.0, ('q23','q61'):-74.0, ('q23','q62'):-148.0, ('q23','q63'):254.0, ('q23','q64'):508.0, ('q24','q25'):-444.0, ('q24','q26'):-888.0, ('q24','q27'):-184.0, ('q24','q28'):-368.0, ('q24','q29'):668.0, ('q24','q30'):1336.0, ('q24','q31'):-296.0, ('q24','q32'):-592.0, ('q24','q33'):640.0, ('q24','q34'):1280.0, ('q24','q35'):60.0, ('q24','q36'):120.0, ('q24','q37'):824.0, ('q24','q38'):1648.0, ('q24','q39'):1732.0, ('q24','q40'):3464.0, ('q24','q41'):112.0, ('q24','q42'):224.0, ('q24','q43'):632.0, ('q24','q44'):1264.0, ('q24','q45'):816.0, ('q24','q46'):1632.0, ('q24','q47'):1704.0, ('q24','q48'):3408.0, ('q24','q49'):-548.0, ('q24','q50'):-1096.0, ('q24','q51'):-848.0, ('q24','q52'):-1696.0, ('q24','q53'):276.0, ('q24','q54'):552.0, ('q24','q55'):-56.0, ('q24','q56'):-112.0, ('q24','q57'):-1140.0, ('q24','q58'):-2280.0, ('q24','q59'):724.0, ('q24','q60'):1448.0, ('q24','q61'):-148.0, ('q24','q62'):-296.0, ('q24','q63'):508.0, ('q24','q64'):1016.0, ('q25','q26'):3140.0, ('q25','q27'):-574.0, ('q25','q28'):-1148.0, ('q25','q29'):-22.0, ('q25','q30'):-44.0, ('q25','q31'):556.0, ('q25','q32'):1112.0, ('q25','q33'):244.0, ('q25','q34'):488.0, ('q25','q37'):-356.0, ('q25','q38'):-712.0, ('q25','q39'):-386.0, ('q25','q40'):-772.0, ('q25','q41'):70.0, ('q25','q42'):140.0, ('q25','q43'):416.0, ('q25','q44'):832.0, ('q25','q45'):-28.0, ('q25','q46'):-56.0, ('q25','q47'):-398.0, ('q25','q48'):-796.0, ('q25','q49'):-426.0, ('q25','q50'):-852.0, ('q25','q51'):208.0, ('q25','q52'):416.0, ('q25','q53'):242.0, ('q25','q54'):484.0, ('q25','q55'):-390.0, ('q25','q56'):-780.0, ('q25','q57'):114.0, ('q25','q58'):228.0, ('q25','q59'):-134.0, ('q25','q60'):-268.0, ('q25','q61'):278.0, ('q25','q62'):556.0, ('q25','q63'):-280.0, ('q25','q64'):-560.0, ('q26','q27'):-1148.0, ('q26','q28'):-2296.0, ('q26','q29'):-44.0, ('q26','q30'):-88.0, ('q26','q31'):1112.0, ('q26','q32'):2224.0, ('q26','q33'):488.0, ('q26','q34'):976.0, ('q26','q37'):-712.0, ('q26','q38'):-1424.0, ('q26','q39'):-772.0, ('q26','q40'):-1544.0, ('q26','q41'):140.0, ('q26','q42'):280.0, ('q26','q43'):832.0, ('q26','q44'):1664.0, ('q26','q45'):-56.0, ('q26','q46'):-112.0, ('q26','q47'):-796.0, ('q26','q48'):-1592.0, ('q26','q49'):-852.0, ('q26','q50'):-1704.0, ('q26','q51'):416.0, ('q26','q52'):832.0, ('q26','q53'):484.0, ('q26','q54'):968.0, ('q26','q55'):-780.0, ('q26','q56'):-1560.0, ('q26','q57'):228.0, ('q26','q58'):456.0, ('q26','q59'):-268.0, ('q26','q60'):-536.0, ('q26','q61'):556.0, ('q26','q62'):1112.0, ('q26','q63'):-560.0, ('q26','q64'):-1120.0, ('q27','q28'):4248.0, ('q27','q29'):-444.0, ('q27','q30'):-888.0, ('q27','q31'):-240.0, ('q27','q32'):-480.0, ('q27','q33'):36.0, ('q27','q34'):72.0, ('q27','q35'):50.0, ('q27','q36'):100.0, ('q27','q37'):-128.0, ('q27','q38'):-256.0, ('q27','q39'):228.0, ('q27','q40'):456.0, ('q27','q41'):154.0, ('q27','q42'):308.0, ('q27','q43'):170.0, ('q27','q44'):340.0, ('q27','q45'):-270.0, ('q27','q46'):-540.0, ('q27','q47'):204.0, ('q27','q48'):408.0, ('q27','q49'):298.0, ('q27','q50'):596.0, ('q27','q51'):-86.0, ('q27','q52'):-172.0, ('q27','q53'):56.0, ('q27','q54'):112.0, ('q27','q55'):54.0, ('q27','q56'):108.0, ('q27','q57'):14.0, ('q27','q58'):28.0, ('q27','q59'):-274.0, ('q27','q60'):-548.0, ('q27','q61'):86.0, ('q27','q62'):172.0, ('q27','q63'):-84.0, ('q27','q64'):-168.0, ('q28','q29'):-888.0, ('q28','q30'):-1776.0, ('q28','q31'):-480.0, ('q28','q32'):-960.0, ('q28','q33'):72.0, ('q28','q34'):144.0, ('q28','q35'):100.0, ('q28','q36'):200.0, ('q28','q37'):-256.0, ('q28','q38'):-512.0, ('q28','q39'):456.0, ('q28','q40'):912.0, ('q28','q41'):308.0, ('q28','q42'):616.0, ('q28','q43'):340.0, ('q28','q44'):680.0, ('q28','q45'):-540.0, ('q28','q46'):-1080.0, ('q28','q47'):408.0, ('q28','q48'):816.0, ('q28','q49'):596.0, ('q28','q50'):1192.0, ('q28','q51'):-172.0, ('q28','q52'):-344.0, ('q28','q53'):112.0, ('q28','q54'):224.0, ('q28','q55'):108.0, ('q28','q56'):216.0, ('q28','q57'):28.0, ('q28','q58'):56.0, ('q28','q59'):-548.0, ('q28','q60'):-1096.0, ('q28','q61'):172.0, ('q28','q62'):344.0, ('q28','q63'):-168.0, ('q28','q64'):-336.0, ('q29','q30'):4812.0, ('q29','q31'):-622.0, ('q29','q32'):-1244.0, ('q29','q33'):-428.0, ('q29','q34'):-856.0, ('q29','q35'):8.0, ('q29','q36'):16.0, ('q29','q37'):284.0, ('q29','q38'):568.0, ('q29','q39'):290.0, ('q29','q40'):580.0, ('q29','q41'):-836.0, ('q29','q42'):-1672.0, ('q29','q43'):-324.0, ('q29','q44'):-648.0, ('q29','q45'):60.0, ('q29','q46'):120.0, ('q29','q47'):-114.0, ('q29','q48'):-228.0, ('q29','q49'):-120.0, ('q29','q50'):-240.0, ('q29','q51'):-176.0, ('q29','q52'):-352.0, ('q29','q53'):-22.0, ('q29','q54'):-44.0, ('q29','q55'):412.0, ('q29','q56'):824.0, ('q29','q57'):-14.0, ('q29','q58'):-28.0, ('q29','q59'):252.0, ('q29','q60'):504.0, ('q29','q61'):554.0, ('q29','q62'):1108.0, ('q29','q63'):74.0, ('q29','q64'):148.0, ('q30','q31'):-1244.0, ('q30','q32'):-2488.0, ('q30','q33'):-856.0, ('q30','q34'):-1712.0, ('q30','q35'):16.0, ('q30','q36'):32.0, ('q30','q37'):568.0, ('q30','q38'):1136.0, ('q30','q39'):580.0, ('q30','q40'):1160.0, ('q30','q41'):-1672.0, ('q30','q42'):-3344.0, ('q30','q43'):-648.0, ('q30','q44'):-1296.0, ('q30','q45'):120.0, ('q30','q46'):240.0, ('q30','q47'):-228.0, ('q30','q48'):-456.0, ('q30','q49'):-240.0, ('q30','q50'):-480.0, ('q30','q51'):-352.0, ('q30','q52'):-704.0, ('q30','q53'):-44.0, ('q30','q54'):-88.0, ('q30','q55'):824.0, ('q30','q56'):1648.0, ('q30','q57'):-28.0, ('q30','q58'):-56.0, ('q30','q59'):504.0, ('q30','q60'):1008.0, ('q30','q61'):1108.0, ('q30','q62'):2216.0, ('q30','q63'):148.0, ('q30','q64'):296.0, ('q31','q32'):5416.0, ('q31','q33'):586.0, ('q31','q34'):1172.0, ('q31','q35'):108.0, ('q31','q36'):216.0, ('q31','q37'):-480.0, ('q31','q38'):-960.0, ('q31','q41'):-176.0, ('q31','q42'):-352.0, ('q31','q43'):110.0, ('q31','q44'):220.0, ('q31','q45'):-490.0, ('q31','q46'):-980.0, ('q31','q47'):-184.0, ('q31','q48'):-368.0, ('q31','q49'):108.0, ('q31','q50'):216.0, ('q31','q51'):86.0, ('q31','q52'):172.0, ('q31','q53'):-422.0, ('q31','q54'):-844.0, ('q31','q55'):-752.0, ('q31','q56'):-1504.0, ('q31','q57'):56.0, ('q31','q58'):112.0, ('q31','q59'):116.0, ('q31','q60'):232.0, ('q31','q61'):46.0, ('q31','q62'):92.0, ('q31','q63'):-90.0, ('q31','q64'):-180.0, ('q32','q33'):1172.0, ('q32','q34'):2344.0, ('q32','q35'):216.0, ('q32','q36'):432.0, ('q32','q37'):-960.0, ('q32','q38'):-1920.0, ('q32','q41'):-352.0, ('q32','q42'):-704.0, ('q32','q43'):220.0, ('q32','q44'):440.0, ('q32','q45'):-980.0, ('q32','q46'):-1960.0, ('q32','q47'):-368.0, ('q32','q48'):-736.0, ('q32','q49'):216.0, ('q32','q50'):432.0, ('q32','q51'):172.0, ('q32','q52'):344.0, ('q32','q53'):-844.0, ('q32','q54'):-1688.0, ('q32','q55'):-1504.0, ('q32','q56'):-3008.0, ('q32','q57'):112.0, ('q32','q58'):224.0, ('q32','q59'):232.0, ('q32','q60'):464.0, ('q32','q61'):92.0, ('q32','q62'):184.0, ('q32','q63'):-180.0, ('q32','q64'):-360.0, ('q33','q34'):5976.0, ('q33','q35'):-334.0, ('q33','q36'):-668.0, ('q33','q37'):242.0, ('q33','q38'):484.0, ('q33','q39'):58.0, ('q33','q40'):116.0, ('q33','q41'):86.0, ('q33','q42'):172.0, ('q33','q43'):100.0, ('q33','q44'):200.0, ('q33','q45'):228.0, ('q33','q46'):456.0, ('q33','q47'):514.0, ('q33','q48'):1028.0, ('q33','q49'):340.0, ('q33','q50'):680.0, ('q33','q51'):-400.0, ('q33','q52'):-800.0, ('q33','q53'):-102.0, ('q33','q54'):-204.0, ('q33','q55'):-670.0, ('q33','q56'):-1340.0, ('q33','q57'):106.0, ('q33','q58'):212.0, ('q33','q59'):-52.0, ('q33','q60'):-104.0, ('q33','q61'):248.0, ('q33','q62'):496.0, ('q33','q63'):502.0, ('q33','q64'):1004.0, ('q34','q35'):-668.0, ('q34','q36'):-1336.0, ('q34','q37'):484.0, ('q34','q38'):968.0, ('q34','q39'):116.0, ('q34','q40'):232.0, ('q34','q41'):172.0, ('q34','q42'):344.0, ('q34','q43'):200.0, ('q34','q44'):400.0, ('q34','q45'):456.0, ('q34','q46'):912.0, ('q34','q47'):1028.0, ('q34','q48'):2056.0, ('q34','q49'):680.0, ('q34','q50'):1360.0, ('q34','q51'):-800.0, ('q34','q52'):-1600.0, ('q34','q53'):-204.0, ('q34','q54'):-408.0, ('q34','q55'):-1340.0, ('q34','q56'):-2680.0, ('q34','q57'):212.0, ('q34','q58'):424.0, ('q34','q59'):-104.0, ('q34','q60'):-208.0, ('q34','q61'):496.0, ('q34','q62'):992.0, ('q34','q63'):1004.0, ('q34','q64'):2008.0, ('q35','q36'):3372.0, ('q35','q37'):122.0, ('q35','q38'):244.0, ('q35','q39'):560.0, ('q35','q40'):1120.0, ('q35','q41'):480.0, ('q35','q42'):960.0, ('q35','q43'):-214.0, ('q35','q44'):-428.0, ('q35','q45'):-400.0, ('q35','q46'):-800.0, ('q35','q47'):178.0, ('q35','q48'):356.0, ('q35','q49'):-238.0, ('q35','q50'):-476.0, ('q35','q51'):472.0, ('q35','q52'):944.0, ('q35','q53'):108.0, ('q35','q54'):216.0, ('q35','q55'):-162.0, ('q35','q56'):-324.0, ('q35','q57'):-590.0, ('q35','q58'):-1180.0, ('q35','q59'):-86.0, ('q35','q60'):-172.0, ('q35','q61'):-208.0, ('q35','q62'):-416.0, ('q35','q63'):-550.0, ('q35','q64'):-1100.0, ('q36','q37'):244.0, ('q36','q38'):488.0, ('q36','q39'):1120.0, ('q36','q40'):2240.0, ('q36','q41'):960.0, ('q36','q42'):1920.0, ('q36','q43'):-428.0, ('q36','q44'):-856.0, ('q36','q45'):-800.0, ('q36','q46'):-1600.0, ('q36','q47'):356.0, ('q36','q48'):712.0, ('q36','q49'):-476.0, ('q36','q50'):-952.0, ('q36','q51'):944.0, ('q36','q52'):1888.0, ('q36','q53'):216.0, ('q36','q54'):432.0, ('q36','q55'):-324.0, ('q36','q56'):-648.0, ('q36','q57'):-1180.0, ('q36','q58'):-2360.0, ('q36','q59'):-172.0, ('q36','q60'):-344.0, ('q36','q61'):-416.0, ('q36','q62'):-832.0, ('q36','q63'):-1100.0, ('q36','q64'):-2200.0, ('q37','q38'):4756.0, ('q37','q39'):286.0, ('q37','q40'):572.0, ('q37','q41'):20.0, ('q37','q42'):40.0, ('q37','q43'):450.0, ('q37','q44'):900.0, ('q37','q45'):394.0, ('q37','q46'):788.0, ('q37','q47'):-210.0, ('q37','q48'):-420.0, ('q37','q49'):-372.0, ('q37','q50'):-744.0, ('q37','q51'):688.0, ('q37','q52'):1376.0, ('q37','q53'):426.0, ('q37','q54'):852.0, ('q37','q55'):426.0, ('q37','q56'):852.0, ('q37','q57'):-156.0, ('q37','q58'):-312.0, ('q37','q59'):350.0, ('q37','q60'):700.0, ('q37','q61'):712.0, ('q37','q62'):1424.0, ('q37','q63'):706.0, ('q37','q64'):1412.0, ('q38','q39'):572.0, ('q38','q40'):1144.0, ('q38','q41'):40.0, ('q38','q42'):80.0, ('q38','q43'):900.0, ('q38','q44'):1800.0, ('q38','q45'):788.0, ('q38','q46'):1576.0, ('q38','q47'):-420.0, ('q38','q48'):-840.0, ('q38','q49'):-744.0, ('q38','q50'):-1488.0, ('q38','q51'):1376.0, ('q38','q52'):2752.0, ('q38','q53'):852.0, ('q38','q54'):1704.0, ('q38','q55'):852.0, ('q38','q56'):1704.0, ('q38','q57'):-312.0, ('q38','q58'):-624.0, ('q38','q59'):700.0, ('q38','q60'):1400.0, ('q38','q61'):1424.0, ('q38','q62'):2848.0, ('q38','q63'):1412.0, ('q38','q64'):2824.0, ('q39','q40'):4036.0, ('q39','q41'):-218.0, ('q39','q42'):-436.0, ('q39','q43'):86.0, ('q39','q44'):172.0, ('q39','q45'):130.0, ('q39','q46'):260.0, ('q39','q47'):750.0, ('q39','q48'):1500.0, ('q39','q49'):392.0, ('q39','q50'):784.0, ('q39','q51'):-268.0, ('q39','q52'):-536.0, ('q39','q53'):594.0, ('q39','q54'):1188.0, ('q39','q55'):360.0, ('q39','q56'):720.0, ('q39','q57'):130.0, ('q39','q58'):260.0, ('q39','q59'):468.0, ('q39','q60'):936.0, ('q39','q61'):28.0, ('q39','q62'):56.0, ('q39','q63'):-350.0, ('q39','q64'):-700.0, ('q40','q41'):-436.0, ('q40','q42'):-872.0, ('q40','q43'):172.0, ('q40','q44'):344.0, ('q40','q45'):260.0, ('q40','q46'):520.0, ('q40','q47'):1500.0, ('q40','q48'):3000.0, ('q40','q49'):784.0, ('q40','q50'):1568.0, ('q40','q51'):-536.0, ('q40','q52'):-1072.0, ('q40','q53'):1188.0, ('q40','q54'):2376.0, ('q40','q55'):720.0, ('q40','q56'):1440.0, ('q40','q57'):260.0, ('q40','q58'):520.0, ('q40','q59'):936.0, ('q40','q60'):1872.0, ('q40','q61'):56.0, ('q40','q62'):112.0, ('q40','q63'):-700.0, ('q40','q64'):-1400.0, ('q41','q42'):5568.0, ('q41','q43'):164.0, ('q41','q44'):328.0, ('q41','q45'):-306.0, ('q41','q46'):-612.0, ('q41','q47'):412.0, ('q41','q48'):824.0, ('q41','q49'):-538.0, ('q41','q50'):-1076.0, ('q41','q51'):494.0, ('q41','q52'):988.0, ('q41','q53'):-138.0, ('q41','q54'):-276.0, ('q41','q55'):56.0, ('q41','q56'):112.0, ('q41','q57'):158.0, ('q41','q58'):316.0, ('q41','q59'):40.0, ('q41','q60'):80.0, ('q41','q61'):-292.0, ('q41','q62'):-584.0, ('q41','q63'):-238.0, ('q41','q64'):-476.0, ('q42','q43'):328.0, ('q42','q44'):656.0, ('q42','q45'):-612.0, ('q42','q46'):-1224.0, ('q42','q47'):824.0, ('q42','q48'):1648.0, ('q42','q49'):-1076.0, ('q42','q50'):-2152.0, ('q42','q51'):988.0, ('q42','q52'):1976.0, ('q42','q53'):-276.0, ('q42','q54'):-552.0, ('q42','q55'):112.0, ('q42','q56'):224.0, ('q42','q57'):316.0, ('q42','q58'):632.0, ('q42','q59'):80.0, ('q42','q60'):160.0, ('q42','q61'):-584.0, ('q42','q62'):-1168.0, ('q42','q63'):-476.0, ('q42','q64'):-952.0, ('q43','q44'):3576.0, ('q43','q45'):-314.0, ('q43','q46'):-628.0, ('q43','q47'):-200.0, ('q43','q48'):-400.0, ('q43','q49'):-344.0, ('q43','q50'):-688.0, ('q43','q51'):80.0, ('q43','q52'):160.0, ('q43','q53'):236.0, ('q43','q54'):472.0, ('q43','q55'):70.0, ('q43','q56'):140.0, ('q43','q57'):-76.0, ('q43','q58'):-152.0, ('q43','q59'):-190.0, ('q43','q60'):-380.0, ('q43','q61'):-114.0, ('q43','q62'):-228.0, ('q43','q63'):10.0, ('q43','q64'):20.0, ('q44','q45'):-628.0, ('q44','q46'):-1256.0, ('q44','q47'):-400.0, ('q44','q48'):-800.0, ('q44','q49'):-688.0, ('q44','q50'):-1376.0, ('q44','q51'):160.0, ('q44','q52'):320.0, ('q44','q53'):472.0, ('q44','q54'):944.0, ('q44','q55'):140.0, ('q44','q56'):280.0, ('q44','q57'):-152.0, ('q44','q58'):-304.0, ('q44','q59'):-380.0, ('q44','q60'):-760.0, ('q44','q61'):-228.0, ('q44','q62'):-456.0, ('q44','q63'):20.0, ('q44','q64'):40.0, ('q45','q46'):4060.0, ('q45','q47'):114.0, ('q45','q48'):228.0, ('q45','q49'):444.0, ('q45','q50'):888.0, ('q45','q51'):-210.0, ('q45','q52'):-420.0, ('q45','q53'):-294.0, ('q45','q54'):-588.0, ('q45','q55'):-186.0, ('q45','q56'):-372.0, ('q45','q57'):158.0, ('q45','q58'):316.0, ('q45','q59'):126.0, ('q45','q60'):252.0, ('q45','q61'):398.0, ('q45','q62'):796.0, ('q45','q63'):358.0, ('q45','q64'):716.0, ('q46','q47'):228.0, ('q46','q48'):456.0, ('q46','q49'):888.0, ('q46','q50'):1776.0, ('q46','q51'):-420.0, ('q46','q52'):-840.0, ('q46','q53'):-588.0, ('q46','q54'):-1176.0, ('q46','q55'):-372.0, ('q46','q56'):-744.0, ('q46','q57'):316.0, ('q46','q58'):632.0, ('q46','q59'):252.0, ('q46','q60'):504.0, ('q46','q61'):796.0, ('q46','q62'):1592.0, ('q46','q63'):716.0, ('q46','q64'):1432.0, ('q47','q48'):3964.0, ('q47','q49'):386.0, ('q47','q50'):772.0, ('q47','q51'):-292.0, ('q47','q52'):-584.0, ('q47','q53'):408.0, ('q47','q54'):816.0, ('q47','q55'):312.0, ('q47','q56'):624.0, ('q47','q57'):-504.0, ('q47','q58'):-1008.0, ('q47','q59'):474.0, ('q47','q60'):948.0, ('q47','q61'):-100.0, ('q47','q62'):-200.0, ('q47','q63'):-76.0, ('q47','q64'):-152.0, ('q48','q49'):772.0, ('q48','q50'):1544.0, ('q48','q51'):-584.0, ('q48','q52'):-1168.0, ('q48','q53'):816.0, ('q48','q54'):1632.0, ('q48','q55'):624.0, ('q48','q56'):1248.0, ('q48','q57'):-1008.0, ('q48','q58'):-2016.0, ('q48','q59'):948.0, ('q48','q60'):1896.0, ('q48','q61'):-200.0, ('q48','q62'):-400.0, ('q48','q63'):-152.0, ('q48','q64'):-304.0, ('q49','q50'):4224.0, ('q49','q51'):-164.0, ('q49','q52'):-328.0, ('q49','q53'):204.0, ('q49','q54'):408.0, ('q49','q55'):-40.0, ('q49','q56'):-80.0, ('q49','q57'):38.0, ('q49','q58'):76.0, ('q49','q59'):-122.0, ('q49','q60'):-244.0, ('q49','q61'):-268.0, ('q49','q62'):-536.0, ('q49','q63'):570.0, ('q49','q64'):1140.0, ('q50','q51'):-328.0, ('q50','q52'):-656.0, ('q50','q53'):408.0, ('q50','q54'):816.0, ('q50','q55'):-80.0, ('q50','q56'):-160.0, ('q50','q57'):76.0, ('q50','q58'):152.0, ('q50','q59'):-244.0, ('q50','q60'):-488.0, ('q50','q61'):-536.0, ('q50','q62'):-1072.0, ('q50','q63'):1140.0, ('q50','q64'):2280.0, ('q51','q52'):4604.0, ('q51','q53'):-150.0, ('q51','q54'):-300.0, ('q51','q55'):-134.0, ('q51','q56'):-268.0, ('q51','q57'):-88.0, ('q51','q58'):-176.0, ('q51','q59'):-472.0, ('q51','q60'):-944.0, ('q51','q61'):232.0, ('q51','q62'):464.0, ('q51','q63'):270.0, ('q51','q64'):540.0, ('q52','q53'):-300.0, ('q52','q54'):-600.0, ('q52','q55'):-268.0, ('q52','q56'):-536.0, ('q52','q57'):-176.0, ('q52','q58'):-352.0, ('q52','q59'):-944.0, ('q52','q60'):-1888.0, ('q52','q61'):464.0, ('q52','q62'):928.0, ('q52','q63'):540.0, ('q52','q64'):1080.0, ('q53','q54'):4740.0, ('q53','q55'):124.0, ('q53','q56'):248.0, ('q53','q57'):90.0, ('q53','q58'):180.0, ('q53','q59'):306.0, ('q53','q60'):612.0, ('q53','q61'):-228.0, ('q53','q62'):-456.0, ('q53','q63'):116.0, ('q53','q64'):232.0, ('q54','q55'):248.0, ('q54','q56'):496.0, ('q54','q57'):180.0, ('q54','q58'):360.0, ('q54','q59'):612.0, ('q54','q60'):1224.0, ('q54','q61'):-456.0, ('q54','q62'):-912.0, ('q54','q63'):232.0, ('q54','q64'):464.0, ('q55','q56'):3344.0, ('q55','q57'):178.0, ('q55','q58'):356.0, ('q55','q59'):98.0, ('q55','q60'):196.0, ('q55','q61'):140.0, ('q55','q62'):280.0, ('q55','q63'):138.0, ('q55','q64'):276.0, ('q56','q57'):356.0, ('q56','q58'):712.0, ('q56','q59'):196.0, ('q56','q60'):392.0, ('q56','q61'):280.0, ('q56','q62'):560.0, ('q56','q63'):276.0, ('q56','q64'):552.0, ('q57','q58'):4220.0, ('q57','q59'):-440.0, ('q57','q60'):-880.0, ('q57','q61'):-94.0, ('q57','q62'):-188.0, ('q57','q63'):-370.0, ('q57','q64'):-740.0, ('q58','q59'):-880.0, ('q58','q60'):-1760.0, ('q58','q61'):-188.0, ('q58','q62'):-376.0, ('q58','q63'):-740.0, ('q58','q64'):-1480.0, ('q59','q60'):3200.0, ('q59','q61'):470.0, ('q59','q62'):940.0, ('q59','q63'):148.0, ('q59','q64'):296.0, ('q60','q61'):940.0, ('q60','q62'):1880.0, ('q60','q63'):296.0, ('q60','q64'):592.0, ('q61','q62'):2860.0, ('q61','q63'):200.0, ('q61','q64'):400.0, ('q62','q63'):400.0, ('q62','q64'):800.0, ('q63','q64'):5108.0}

Q = dict(linear)
Q.update(quadratic)

sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
9338  0   0   1   0   1   1   0   0   1   0   1  0 ...  0 -156532.0       1 ...
8821  0   0   1   0   1   1   0   0   0   0   1  0 ...  0 -156439.0       1 ...
24    0   0   1   0   1   1   0   0   0   0   0  1 ...  0 -155806.0       1 ...
37    1   0   1   0   1   1   0   0   1   0   0  1 ...  0 -155490.0       1 ...
3326  1   0   1   0   1   1   0   0   0   0   0  0 ...  0 -155190.0       1 ...
6403  0   0   1   0   1   1   0   0   0   0   0  1 ...  1 -154973.0       1 ...
9322  0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -154787.0       1 ...
9395  1   0   1   0   0   1   0   0   0   0   0  1 ...  1 -154729.0       1 ...
6745  1   0   0   1   1   1   0   0   0   0   1  1 ...  1 -154708.0       1 ...
1170  0   0   0   1   1   1   0   0   1   0   1  1 ...  1 -154566.0       1 ...
2446  1   0   0   1   1   1   1   0   1   0   1  1 ...  0 -154312.0       1 ...
5003  1   0   0   1   1   1   0   0   0 

In [8]:
sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
5002  0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -156279.0       1 ...
1283  0   0   0   1   0   1   1   0   0   0   1  1 ...  0 -156057.0       1 ...
26    1   0   1   0   1   1   0   0   0   0   1  1 ...  0 -155670.0       1 ...
43    0   0   1   0   1   1   0   0   0   0   0  1 ...  0 -155655.0       1 ...
3479  0   0   1   0   1   1   0   0   0   0   1  1 ...  1 -155600.0       1 ...
16    1   0   1   0   1   1   0   0   0   0   1  0 ...  1 -155579.0       1 ...
3747  0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -155410.0       1 ...
1686  0   0   0   1   1   1   0   0   0   0   1  1 ...  1 -155254.0       1 ...
683   1   0   1   0   1   1   0   0   0   0   1  0 ...  0 -155184.0       1 ...
357   0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -155133.0       1 ...
4443  0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -155132.0       1 ...
4327  0   0   1   0   1   1   1   0   1 

In [9]:
sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
698   1   0   0   1   1   1   1   0   1   0   1  1 ...  0 -156402.0       1 ...
682   0   0   0   1   1   1   0   0   0   0   1  1 ...  0 -155671.0       1 ...
5400  1   0   0   1   1   1   0   0   0   1   1  0 ...  0 -155664.0       1 ...
918   0   0   0   1   1   1   0   0   1   0   1  1 ...  0 -155397.0       1 ...
2967  1   0   0   1   1   1   0   0   1   0   1  0 ...  0 -155090.0       1 ...
783   0   0   1   0   1   1   0   0   0   0   0  1 ...  0 -155007.0       1 ...
459   1   0   0   1   1   1   1   0   0   0   1  1 ...  0 -154770.0       1 ...
1179  1   0   0   1   1   1   0   0   0   0   0  0 ...  0 -154666.0       1 ...
853   0   0   0   1   1   1   0   0   0   0   1  0 ...  0 -154643.0       1 ...
208   1   0   1   0   1   1   0   0   0   0   1  0 ...  0 -154642.0       1 ...
7956  0   0   1   0   1   1   0   0   1   0   0  1 ...  0 -154586.0       1 ...
628   0   0   1   0   1   1   0   0   1 

In [10]:
sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
6143  0   0   1   0   0   1   0   0   0   0   1  1 ...  0 -159397.0       1 ...
647   1   0   1   0   0   1   0   0   0   0   1  0 ...  0 -158656.0       1 ...
2486  1   0   1   0   0   1   0   0   0   0   0  1 ...  0 -157337.0       1 ...
9354  1   0   1   0   1   1   0   0   0   0   0  1 ...  0 -156972.0       1 ...
603   1   0   1   0   1   1   0   0   0   0   1  0 ...  0 -156448.0       1 ...
3162  0   0   1   0   0   1   0   0   1   0   1  1 ...  0 -156217.0       1 ...
1618  1   0   1   0   0   1   0   0   0   0   0  0 ...  0 -156096.0       1 ...
1668  1   0   1   0   1   1   0   0   1   0   1  0 ...  0 -155948.0       1 ...
4498  1   0   1   0   1   1   0   0   0   1   1  0 ...  1 -155887.0       1 ...
1877  1   0   1   0   1   1   0   0   0   0   1  0 ...  0 -155872.0       1 ...
2928  0   0   1   0   0   1   0   0   0   0   1  1 ...  0 -155830.0       1 ...
355   1   0   1   0   0   1   0   0   0 

In [11]:
sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
528   0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -156999.0       1 ...
971   0   0   1   0   1   1   0   0   0   0   0  1 ...  0 -156310.0       1 ...
5262  0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -156295.0       1 ...
12    0   0   1   0   1   1   1   0   0   0   0  1 ...  0 -156260.0       1 ...
210   0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -156025.0       1 ...
60    0   0   1   0   1   1   0   0   1   0   1  1 ...  0 -155928.0       1 ...
1183  0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -155827.0       1 ...
5990  0   0   1   0   1   1   1   0   0   0   0  0 ...  0 -155806.0       1 ...
7665  0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -155715.0       1 ...
95    0   0   1   0   1   1   0   0   0   0   1  1 ...  0 -155638.0       1 ...
21    0   0   1   0   1   1   0   0   0   0   0  1 ...  1 -155059.0       1 ...
42    0   0   1   0   1   1   0   0   0 

In [12]:
sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
1281  1   0   0   1   1   1   0   0   0   0   1  0 ...  0 -156837.0       1 ...
1687  1   0   0   1   1   1   0   0   0   0   1  0 ...  0 -156634.0       1 ...
2304  1   0   0   1   1   1   0   0   1   0   1  0 ...  0 -156372.0       1 ...
132   0   0   0   1   1   1   0   0   0   0   1  0 ...  0 -156266.0       1 ...
200   1   0   0   1   1   1   0   0   1   0   1  0 ...  0 -156195.0       1 ...
5857  1   0   0   1   1   1   0   0   1   0   1  0 ...  0 -155859.0       1 ...
207   0   0   0   1   1   1   0   0   0   0   1  0 ...  0 -155838.0       1 ...
3144  0   0   0   1   1   1   1   0   0   0   1  0 ...  0 -155695.0       1 ...
111   1   0   0   1   1   1   0   0   0   0   1  0 ...  0 -155689.0       1 ...
3679  1   0   0   1   1   1   0   0   0   0   0  0 ...  0 -155648.0       1 ...
452   1   0   1   0   1   1   0   0   0   0   1  0 ...  0 -155638.0       1 ...
6959  1   0   0   1   1   1   0   0   1 

In [13]:
sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
102   0   0   1   0   1   1   0   0   1   0   0  1 ...  0 -158230.0       1 ...
955   1   0   0   1   0   1   1   0   0   0   1  1 ...  0 -157414.0       1 ...
8725  1   0   0   1   1   1   1   0   0   0   1  1 ...  0 -156739.0       1 ...
44    1   0   1   0   1   1   0   0   0   0   1  0 ...  0 -156703.0       1 ...
1     0   0   1   0   1   1   0   0   0   1   1  1 ...  0 -156652.0       1 ...
195   1   0   0   1   0   1   1   0   0   0   1  1 ...  0 -156562.0       1 ...
4097  1   0   1   0   1   1   0   0   1   0   1  0 ...  0 -156561.0       1 ...
5669  1   0   1   0   1   1   0   0   1   0   1  1 ...  0 -156428.0       1 ...
471   0   0   1   0   1   1   0   0   1   0   1  1 ...  0 -156284.0       1 ...
4356  0   0   1   0   1   1   0   0   1   0   1  1 ...  0 -156251.0       1 ...
789   1   0   1   0   1   1   0   0   0   0   1  0 ...  0 -156171.0       1 ...
7022  0   0   0   1   1   1   1   0   0 

In [14]:
sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
825   1   0   1   0   1   1   0   0   1   0   1  0 ...  0 -157840.0       1 ...
293   0   0   1   0   1   1   0   0   1   0   1  1 ...  0 -156572.0       1 ...
1231  0   0   1   0   1   1   0   0   1   0   1  0 ...  0 -156449.0       1 ...
367   1   0   1   0   0   1   0   0   0   0   1  0 ...  0 -156265.0       1 ...
2     1   0   1   0   1   1   0   0   1   0   1  0 ...  0 -156112.0       1 ...
1075  1   0   1   0   1   1   0   0   1   0   1  0 ...  0 -156053.0       1 ...
9585  1   0   1   0   0   1   0   0   0   0   1  0 ...  0 -155928.0       1 ...
194   1   0   1   0   1   1   0   0   1   0   1  0 ...  0 -155763.0       1 ...
3371  1   0   1   0   1   1   0   0   0   0   1  0 ...  0 -155741.0       1 ...
2811  1   0   1   0   1   1   0   0   0   0   1  0 ...  0 -155721.0       1 ...
679   0   0   1   0   1   1   0   0   1   0   1  0 ...  0 -155647.0       1 ...
3297  0   0   1   0   1   1   1   0   1 

In [15]:
sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
2491  0   0   0   1   0   1   0   0   0   0   0  1 ...  0 -158070.0       1 ...
4425  0   0   0   0   0   1   0   0   0   0   1  1 ...  0 -157867.0       1 ...
5611  0   0   0   1   1   0   0   0   0   0   0  1 ...  0 -157544.0       1 ...
735   0   0   1   0   0   1   1   0   0   0   0  1 ...  0 -157375.0       1 ...
459   1   0   0   1   1   1   0   0   0   0   1  0 ...  0 -157134.0       1 ...
108   0   0   0   1   0   1   1   0   0   0   1  1 ...  0 -157077.0       1 ...
1174  0   0   0   1   1   1   1   0   0   0   0  1 ...  0 -156920.0       1 ...
2706  0   0   0   1   1   1   0   0   0   0   1  1 ...  0 -156915.0       1 ...
8736  0   0   1   0   0   1   0   0   0   0   1  1 ...  0 -156799.0       1 ...
1225  1   0   0   0   1   1   0   0   1   0   1  0 ...  0 -156750.0       1 ...
909   0   0   1   0   1   1   0   0   1   0   1  1 ...  0 -156649.0       1 ...
1993  1   0   0   1   0   1   0   0   0 

In [16]:
sampleset = sampler_auto.sample_qubo(Q, num_reads=10000)
print(sampleset)

     q1 q10 q11 q12 q13 q14 q15 q16 q17 q18 q19 q2 ... q9    energy num_oc. ...
2764  1   0   1   0   1   1   0   0   0   0   0  1 ...  0 -154769.0       1 ...
6051  0   0   0   1   1   1   0   0   0   0   0  1 ...  0 -154046.0       1 ...
8541  1   0   0   1   1   1   1   0   0   0   1  1 ...  1 -153905.0       1 ...
184   0   1   0   1   1   1   0   1   0   0   0  1 ...  0 -153870.0       1 ...
9323  1   0   0   1   0   1   0   0   0   0   0  1 ...  0 -153725.0       1 ...
4767  0   0   0   1   0   1   0   1   0   0   0  0 ...  0 -153690.0       1 ...
400   1   0   0   1   1   0   0   0   0   0   0  1 ...  0 -153612.0       1 ...
1183  0   0   0   1   1   1   0   0   0   0   1  1 ...  0 -153579.0       1 ...
4468  1   0   0   1   1   1   1   0   0   0   0  0 ...  0 -153441.0       1 ...
4971  1   0   0   1   0   1   1   0   0   0   0  1 ...  0 -153420.0       1 ...
5983  0   0   0   1   1   1   0   0   0   0   0  1 ...  0 -153361.0       1 ...
7684  1   0   0   1   1   1   0   0   0 